# Peer-graded Assignment: Capstone Project - The Battle of Neighborhoods (Week 1)  
## Shu Yoko
### Aug 9

Now that you have been equipped with the skills and the tools to use location data to explore a geographical location, over the course of two weeks, you will have the opportunity to be as creative as you want and come up with an idea to leverage the Foursquare location data to explore or compare neighborhoods or cities of your choice or to come up with a problem that you can use the Foursquare location data to solve. If you cannot think of an idea or a problem, here are some ideas to get you started:

1. In Module 3, we explored New York City and the city of Toronto and segmented and clustered their neighborhoods. Both cities are very diverse and are the financial capitals of their respective countries. One interesting idea would be to compare the neighborhoods of the two cities and determine how similar or dissimilar they are. Is New York City more like Toronto or Paris or some other multicultural city? I will leave it to you to refine this idea.
2. In a city of your choice, if someone is looking to open a restaurant, where would you recommend that they open it? Similarly, if a contractor is trying to start their own business, where would you recommend that they setup their office?

These are just a couple of many ideas and problems that can be solved using location data in addition to other datasets. No matter what you decide to do, make sure to provide sufficient justification of why you think what you want to do or solve is important and why would a client or a group of people be interested in your project.

### Week 1 

For this week, you will required to submit the following:

A description of the problem and a discussion of the background. (15 marks)
A description of the data and how it will be used to solve the problem. (15 marks)

## 1. Clearly define a problem or an idea of your choice, where you would need to leverage the Foursquare location data to solve or execute. Remember that data science problems always target an audience and are meant to help a group of stakeholders solve a problem, so make sure that you explicitly describe your audience and why they would care about your problem.

In my project, I will run the hypothesis test about the **hotelling's law** to see if it's actually decent economical strategies. 

Hotelling Law is that: 
*Suppose there are two competing shops located along the length of a street running north and south, with customers spread equally along the street. Both shop owners want their shops to be where they will get most market share of customers. If both shops sell the same range of goods at the same prices then the locations of the shops are themselves the 'products'. Each customer will always choose the nearer shop as it is disadvantageous to travel to the farther. - Wikipedia*. 
[For more discription](https://en.wikipedia.org/wiki/Hotelling's_law)

Basically, this theory argues that if the shops offer the similar products, the shop with most dominant area will win. Here is some figure that explain. Let's say there are two stores A and B. If they decided to open their shop in a linear city that has 12 dashes of land.  

|------|------|   

First, they build the shop as they can share same amount of customer. They both win ------ (6 dashes) of the area/customers that are coming from.    
|---A---|---B---|   

But if B moves 2 dashes closer to shop A.  

|---A--**-|-B-----**|   

Shop B wins some of A's customers since they sell similar products and customer choose to go to the closer shop. A loses some of its customers.  

So A decided to move towards shop B, so A can win some customers too.  

|------A|B------|  

Here, both shops end up with locating at the center.  

Likewise, this theory argues that if the shop was located away from the center, they will loose the competition.  
|--A--**--|-B-----**|  

In this project, I will test if this theory is correct at the city in Manhattan.  
The reason why I chose Manhattan for this project is that Manhattan is a island like shape and is isolated from other land. So I thought that it is easy to calculate the center of the Manhattan.  

## 2. Describe the data that you will be using to solve the problem or execute your idea. Remember that you will need to use the Foursquare location data to solve the problem or execute your idea. You can absolutely use other datasets in combination with the Foursquare location data. So make sure that you provide adequate explanation and discussion, with examples, of the data that you will be using, even if it is only Foursquare location data.

I will use Forsquare data in Manhattan. For all pizza restaurants (stc) in Manhattan with similar rate and similar price, I will see if the pizza restaurants in the near the center of Manhattan has more reviews (# of customers).     

In [357]:
import requests # library to handle requests
import pandas as pd # library for data analsysis
import numpy as np # library to handle data in a vectorized manner
import random # library for random number generation


#pip install geopy
from geopy.geocoders import Nominatim # module to convert an address into latitude and longitude values

# libraries for displaying images
from IPython.display import Image 
from IPython.core.display import HTML 
    
# tranforming json file into a pandas dataframe library
from pandas.io.json import json_normalize


#! pip install folium==0.5.0
import folium # plotting library
import time
import tqdm
from tqdm.notebook import trange, tqdm
from time import sleep



print('Folium installed')
print('Libraries imported.')

Folium installed
Libraries imported.


In [347]:
CLIENT_ID = 'USWT23SP2JAKIN4FPXBP1JNHW3BNMMGD42YV2FKSQFYUVQIM' # your Foursquare ID
CLIENT_SECRET = 'LUB4B1HJET4EAXBHJG5APWOHBYQ13HXTBTWABOP1TZL2EEJT' # your Foursquare Secret
ACCESS_TOKEN = 'RM41FCWJOEZTN0LJOJJJMI3FHVOUQSOLHAHHORHBSG205TXY' # your FourSquare Access Token
VERSION = '20180604'
LIMIT = 50
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: USWT23SP2JAKIN4FPXBP1JNHW3BNMMGD42YV2FKSQFYUVQIM
CLIENT_SECRET:LUB4B1HJET4EAXBHJG5APWOHBYQ13HXTBTWABOP1TZL2EEJT


In [348]:
# radius: 2210
addresses_1 = ['Broadway E Houston St', '7th Ave & W 51st St, New York City', '40.79326,-73.95746']
# radius 1180
addresses_2 = ['40.819187, -73.946999']
# radius 640. 
addresses_3 = ['Broadway W 162nd st, New York', 'Broadway W 178th St, New York', '40.85877,-73.93012', 'Broadway W 207th st']
rad_1 = 2210
rad_2 = 1180
rad_3 = 640

In [349]:
for n in addresses_2:
    address = n
    geolocator = Nominatim(user_agent="foursquare_agent")
    location = geolocator.geocode(address)
    latitude = location.latitude
    longitude = location.longitude
    print(latitude, longitude)

40.8192933 -73.94666146798247


In [350]:
venues = []
for n in addresses_1:
    address = n
    geolocator = Nominatim(user_agent="foursquare_agent")
    location = geolocator.geocode(address)
    latitude = location.latitude
    longitude = location.longitude
    search_query = 'Pizza'
    radius = rad_1
    url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&oauth_token={}&v={}&query={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude,ACCESS_TOKEN, VERSION, search_query, radius, LIMIT)
    results = requests.get(url).json()
    venue = results['response']['venues']
    venues.append(venue)

for n in addresses_2:
    address = n
    geolocator = Nominatim(user_agent="foursquare_agent")
    location = geolocator.geocode(address)
    latitude = location.latitude
    longitude = location.longitude
    search_query = 'Pizza'
    radius = rad_2
    url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&oauth_token={}&v={}&query={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude,ACCESS_TOKEN, VERSION, search_query, radius, LIMIT)
    results = requests.get(url).json()
    venue = results['response']['venues']
    venues.append(venue)
    
for n in addresses_3:
    address = n
    geolocator = Nominatim(user_agent="foursquare_agent")
    location = geolocator.geocode(address)
    latitude = location.latitude
    longitude = location.longitude
    search_query = 'Pizza'
    radius = rad_3
    url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&oauth_token={}&v={}&query={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude,ACCESS_TOKEN, VERSION, search_query, radius, LIMIT)
    results = requests.get(url).json()
    venue = results['response']['venues']
    venues.append(venue)



In [351]:
kk = pd.DataFrame()
for i in venues:
    neighborhood_data = pd.json_normalize(i)
    kk = pd.concat([neighborhood_data, kk])

id                        name  \
0    4ab97430f964a520727f20e3  Grandpa's Brick Oven Pizza   
1    4d77b1c378d5a093829c8372                 Pizza Haven   
2    4c3b4de31a1cd13af120b60d  Tony's Pizza, Pasta & Gyro   
3    4eaae8ff82312ec2f6b379a9                Pizza buffet   
4    5053b972e4b04df233bdabdf                 Pizza Night   
..                        ...                         ...   
260  5078dc5ee4b00760ca933e8f         AKA 99¢ Fresh Pizza   
261  4c6f6888d97fa1434428f3ca    Rocky's Pizza Restaurant   
262  4c9d5b877c096dcbe9abcad1               FDR 99¢ Pizza   
263  4c5b0941b05c1b8dffb9d9b1              Domino's Pizza   
264  5679bd36498e2adeb0c23404          Gini's Pizza Joint   

                                            categories    referralId  hasPerk  \
0    [{'id': '4bf58dd8d48988d1ca941735', 'name': 'P...  v-1629262489    False   
1    [{'id': '4bf58dd8d48988d1ca941735', 'name': 'P...  v-1629262489    False   
2    [{'id': '4bf58dd8d48988d1ca941735', 'name': 'P...  v-1629262489    False   
3    [{'id': '4bf58dd8d48988d1ca941735', 'name': 'P...  v-1629262489    False   
4    [{'id': '4bf58dd8d48988d1ca941735', 'name': 'P...  v-1629262489    False   
..                                                 ...           ...      ...   
260  [{'id': '4bf58dd8d48988d1ca941735', 'name': 'P...  v-1629262483    False   
261  [{'id': '4bf58dd8d48988d1ca941735', 'name': 'P...  v-1629262483    False   
262  [{'id': '4bf58dd8d48988d1ca941735', 'name': 'P...  v-1629262483    False   
263  [{'id': '4bf58dd8d48988d1ca941735', 'name': 'P...  v-1629262483    False   
264  [{'id': '4bf58dd8d48988d1ca941735', 'name': 'P...  v-1629262483    False   

     location.address       location.crossStreet  location.lat  location.lng  \
0       4973 Broadway               Isham Street     40.868215    -73.919419   
1       4942 Broadway                   207th St     40.867700    -73.920812   
2       4771 Broadway                Dyckman St.     40.865608    -73.926851   
3                 NaN                        NaN     40.866776    -73.920807   
4                 NaN                        NaN     40.867998    -73.926105   
..                ...                        ...           ...           ...   
260    117 Orchard St  Btwn Delancey & Rivington     40.719254    -73.989562   
261     304 W 14th St        btwn 8th & 9th Ave.     40.739742    -74.003013   
262      150 E 2nd St          btwn Avenue A & B     40.722915    -73.985619   
263     181 Church St                   Duane St     40.715625    -74.007131   
264  126 Lafayette St                        NaN     40.718724    -74.000045   

                               location.labeledLatLngs  ...  location.country  \
0    [{'label': 'display', 'lat': 40.86821549098444...  ...     United States   
1    [{'label': 'display', 'lat': 40.86770033238289...  ...     United States   
2    [{'label': 'display', 'lat': 40.86560754204715...  ...     United States   
3    [{'label': 'display', 'lat': 40.86677551269531...  ...     United States   
4    [{'label': 'display', 'lat': 40.867998, 'lng':...  ...     United States   
..                                                 ...  ...               ...   
260  [{'label': 'display', 'lat': 40.7192539686804,...  ...     United States   
261  [{'label': 'display', 'lat': 40.739742, 'lng':...  ...     United States   
262  [{'label': 'display', 'lat': 40.72291478323215...  ...     United States   
263  [{'label': 'display', 'lat': 40.71562501338636...  ...     United States   
264  [{'label': 'display', 'lat': 40.71872412978057...  ...     United States   

                             location.formattedAddress delivery.id  \
0    [4973 Broadway (Isham Street), New York, NY 10...         NaN   
1       [4942 Broadway (207th St), New York, NY 10034]       25779   
2    [4771 Broadway (Dyckman St.), New York, NY 10034]         NaN   
3                                                  NaN         NaN   
4                                 [Ne

In [374]:
neighborhoods_data = kk.reset_index(drop=True)

In [370]:
# create map of New York using latitude and longitude values

map_trnt = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng in zip(neighborhoods_data['location.lat'], neighborhoods_data['location.lng']):
    label = '{}'.format(neighborhoods_data)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_trnt)  
    
map_trnt

In [388]:
results

{'meta': {'code': 429,
  'errorType': 'quota_exceeded',
  'errorDetail': 'Quota exceeded',
  'requestId': '611c946ea76264798c668527'},
 'response': {}}

Get detailes of Vebues

KeyError: 'venue'

In [380]:
df = []
for n in trange(len(neighborhoods_data)):
    id = neighborhoods_data['id'][n]
    url =  "https://api.foursquare.com/v2/venues/{}?client_id={}&client_secret={}&ll={},{}&oauth_token={}&v={}&query={}&radius={}&limit={}".format(id,CLIENT_ID, CLIENT_SECRET, latitude, longitude,ACCESS_TOKEN, VERSION, search_query, radius, LIMIT)
    results = requests.get(url).json()
    venue = results['response']['venue']
    df.append(venue)
    time.sleep(5)

  0%|          | 0/265 [00:00<?, ?it/s]

KeyError: 'venue'

In [381]:
results

{'meta': {'code': 429,
  'errorType': 'quota_exceeded',
  'errorDetail': 'Quota exceeded',
  'requestId': '611c940b153c6f11746cc945'},
 'response': {}}

In [382]:
id

'4ab97430f964a520727f20e3'

In [386]:
url =  "https://api.foursquare.com/v2/venues/4ab97430f964a520727f20e3?client_id={}&client_secret={}&ll={},{}&oauth_token={}&v={}&query={}&radius={}&limit={}".format(CLIENT_ID, CLIENT_SECRET, latitude, longitude,ACCESS_TOKEN, VERSION, search_query, radius, LIMIT)
results = requests.get(url).json()
venue = results['response']['venues']
df.append(venue)
time.sleep(5)

KeyError: 'venues'

In [385]:
results

{'meta': {'code': 429,
  'errorType': 'quota_exceeded',
  'errorDetail': 'Quota exceeded',
  'requestId': '611c943d628fec723fb7a217'},
 'response': {}}